In [326]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn import linear_model, metrics
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Ridge
from sklearn.linear_model import Lasso
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_squared_error, r2_score

import os

# hide warnings
import warnings
warnings.filterwarnings('ignore')

In [327]:
df=pd.read_csv('train.csv')

In [328]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1460 entries, 0 to 1459
Data columns (total 81 columns):
Id               1460 non-null int64
MSSubClass       1460 non-null int64
MSZoning         1460 non-null object
LotFrontage      1201 non-null float64
LotArea          1460 non-null int64
Street           1460 non-null object
Alley            91 non-null object
LotShape         1460 non-null object
LandContour      1460 non-null object
Utilities        1460 non-null object
LotConfig        1460 non-null object
LandSlope        1460 non-null object
Neighborhood     1460 non-null object
Condition1       1460 non-null object
Condition2       1460 non-null object
BldgType         1460 non-null object
HouseStyle       1460 non-null object
OverallQual      1460 non-null int64
OverallCond      1460 non-null int64
YearBuilt        1460 non-null int64
YearRemodAdd     1460 non-null int64
RoofStyle        1460 non-null object
RoofMatl         1460 non-null object
Exterior1st      1460 non-n

In [329]:
df.head()

Id  MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0   1          60       RL         65.0     8450   Pave   NaN      Reg   
1   2          20       RL         80.0     9600   Pave   NaN      Reg   
2   3          60       RL         68.0    11250   Pave   NaN      IR1   
3   4          70       RL         60.0     9550   Pave   NaN      IR1   
4   5          60       RL         84.0    14260   Pave   NaN      IR1   

  LandContour Utilities  ... PoolArea PoolQC Fence MiscFeature MiscVal MoSold  \
0         Lvl    AllPub  ...        0    NaN   NaN         NaN       0      2   
1         Lvl    AllPub  ...        0    NaN   NaN         NaN       0      5   
2         Lvl    AllPub  ...        0    NaN   NaN         NaN       0      9   
3         Lvl    AllPub  ...        0    NaN   NaN         NaN       0      2   
4         Lvl    AllPub  ...        0    NaN   NaN         NaN       0     12   

  YrSold  SaleType  SaleCondition  SalePrice  
0   2008        WD         Normal     208500  
1   2007        WD         Normal     181500  
2   2008        WD         Normal     223500  
3   2006        WD        Abnorml     140000  
4   2008        WD         Normal     250000  

[5 rows x 81 columns]

In [330]:
df['Remodeled']=df['YearRemodAdd'].apply(lambda x: '<25years' if 2022-x<=25 else '>25years')

In [331]:
df.drop(['YearRemodAdd'], axis=1, inplace = True)

In [332]:
df['YearBuiltGrp']=(df['YearBuilt']//100)*100

In [333]:
df.drop(['YearBuilt'], axis=1, inplace = True)

In [334]:
df['GarageYrBltGrp']=(df['GarageYrBlt']//100)*100
df.drop(['GarageYrBlt'], axis=1, inplace = True)

In [335]:
df['YrSoldGrp']=df['YrSold'].apply(lambda x: 'Before2008' if x<2008 else 'After2008')
df.drop(['YrSold'], axis=1, inplace = True)

In [336]:
df['MoSoldGrp']=df['MoSold'].apply(lambda x: '1sthalf' if x<=6 else '2ndhalf')
df.drop(['MoSold'], axis=1, inplace = True)

In [337]:
df.shape

(1460, 81)

### Missing value imputation

In [338]:
#Checking for columns with null or missing values
df.isna().any()[lambda x: x] 

LotFrontage       True
Alley             True
MasVnrType        True
MasVnrArea        True
BsmtQual          True
BsmtCond          True
BsmtExposure      True
BsmtFinType1      True
BsmtFinType2      True
Electrical        True
FireplaceQu       True
GarageType        True
GarageFinish      True
GarageQual        True
GarageCond        True
PoolQC            True
Fence             True
MiscFeature       True
GarageYrBltGrp    True
dtype: bool

In [339]:
df['LotFrontage'].isna().sum()

259

In [340]:
# I did some research to find if LotFrontage can be derived or calculated from other columns. I could only find that LotFrontage is a measurement and not a value that can be calculated.
# Since this cant be calculated, I am going ahead with filling the missing values with zeros.

In [341]:
df['LotFrontage'].fillna(value=0, inplace=True)

In [342]:
df.isna().any()[lambda x: x] 

Alley             True
MasVnrType        True
MasVnrArea        True
BsmtQual          True
BsmtCond          True
BsmtExposure      True
BsmtFinType1      True
BsmtFinType2      True
Electrical        True
FireplaceQu       True
GarageType        True
GarageFinish      True
GarageQual        True
GarageCond        True
PoolQC            True
Fence             True
MiscFeature       True
GarageYrBltGrp    True
dtype: bool

In [343]:
#As per the Data dictionary definition, Alley with 'NA' value refers to houses with No Alley access.
# Hence these are not to be treated as missing values. These houses are of category "No Alley"
# we can fill the NA values with "NoAlley" so that the NA is not termed as null values.

In [344]:
df['Alley'].isna().sum()

1369

In [345]:
df['Alley'].fillna(value='NoAlley', inplace=True)

In [346]:
df.isna().any()[lambda x: x] 

MasVnrType        True
MasVnrArea        True
BsmtQual          True
BsmtCond          True
BsmtExposure      True
BsmtFinType1      True
BsmtFinType2      True
Electrical        True
FireplaceQu       True
GarageType        True
GarageFinish      True
GarageQual        True
GarageCond        True
PoolQC            True
Fence             True
MiscFeature       True
GarageYrBltGrp    True
dtype: bool

In [347]:
df['MasVnrType'].isna().sum()

8

In [348]:
# MasVnrType has only 8 missing values. 

In [349]:
df.groupby(['MasVnrType']).count()

Id  MSSubClass  MSZoning  LotFrontage  LotArea  Street  Alley  \
MasVnrType                                                                   
BrkCmn       15          15        15           15       15      15     15   
BrkFace     445         445       445          445      445     445    445   
None        864         864       864          864      864     864    864   
Stone       128         128       128          128      128     128    128   

            LotShape  LandContour  Utilities  ...  MiscFeature  MiscVal  \
MasVnrType                                    ...                         
BrkCmn            15           15         15  ...            2       15   
BrkFace          445          445        445  ...           11      445   
None             864          864        864  ...           40      864   
Stone            128          128        128  ...            1      128   

            SaleType  SaleCondition  SalePrice  Remodeled  YearBuiltGrp  \
MasVnrType                                                                
BrkCmn            15             15         15         15            15   
BrkFace          445            445        445        445           445   
None             864            864        864        864           864   
Stone            128            128        128        128           128   

            GarageYrBltGrp  YrSoldGrp  MoSoldGrp  
MasVnrType                                        
BrkCmn                  15         15         15  
BrkFace                439        445        445  
None                   789        864        864  
Stone                  128        128        128  

[4 rows x 80 columns]

In [350]:
df.groupby(['MasVnrType']).describe()

Id                                                        \
            count        mean         std   min     25%    50%      75%   
MasVnrType                                                                
BrkCmn       15.0  563.466667  365.587564  84.0  262.00  511.0   734.00   
BrkFace     445.0  707.314607  415.313097   1.0  343.00  696.0  1044.00   
None        864.0  739.215278  421.292691   2.0  383.75  744.5  1109.50   
Stone       128.0  764.164062  450.984501   7.0  336.25  805.0  1166.25   

                   MSSubClass             ... YearBuiltGrp          \
               max      count       mean  ...          75%     max   
MasVnrType                                ...                        
BrkCmn      1288.0       15.0  32.666667  ...       1900.0  1900.0   
BrkFace     1453.0      445.0  60.292135  ...       2000.0  2000.0   
None        1460.0      864.0  56.059028  ...       1900.0  2000.0   
Stone       1457.0      128.0  54.179688  ...       2000.0  2000.0   

           GarageYrBltGrp                                                  \
                    count         mean        std     min     25%     50%   
MasVnrType                                                                  
BrkCmn               15.0  1900.000000   0.000000  1900.0  1900.0  1900.0   
BrkFace             439.0  1931.207289  46.386803  1900.0  1900.0  1900.0   
None                789.0  1919.011407  39.263992  1900.0  1900.0  1900.0   
Stone               128.0  1984.375000  36.451888  1900.0  2000.0  2000.0   

                            
               75%     max  
MasVnrType                  
BrkCmn      1900.0  1900.0  
BrkFace     2000.0  2000.0  
None        1900.0  2000.0  
Stone       2000.0  2000.0  

[4 rows x 280 columns]

In [351]:
df[df['MasVnrType'].isna()].describe()

Id  MSSubClass  LotFrontage       LotArea  OverallQual  \
count     8.000000    8.000000     8.000000      8.000000      8.00000   
mean    853.500000   47.500000    55.500000  12250.500000      7.25000   
std     358.316301   35.355339    40.348482   8720.681035      1.28174   
min     235.000000   20.000000     0.000000   4274.000000      6.00000   
25%     620.750000   20.000000    26.250000   8056.500000      6.75000   
50%     955.500000   40.000000    66.000000   9778.000000      7.00000   
75%    1044.500000   60.000000    80.000000  12202.000000      7.25000   
max    1279.000000  120.000000   107.000000  32668.000000     10.00000   

       OverallCond  MasVnrArea   BsmtFinSF1  BsmtFinSF2    BsmtUnfSF  ...  \
count     8.000000         0.0     8.000000         8.0     8.000000  ...   
mean      4.875000         NaN   746.625000         0.0   598.000000  ...   
std       0.834523         NaN   521.198053         0.0   427.175441  ...   
min       3.000000         NaN     0.000000         0.0   135.000000  ...   
25%       5.000000         NaN   468.750000         0.0   301.750000  ...   
50%       5.000000         NaN   818.500000         0.0   516.500000  ...   
75%       5.000000         NaN  1134.250000         0.0   813.750000  ...   
max       6.000000         NaN  1386.000000         0.0  1428.000000  ...   

       WoodDeckSF  OpenPorchSF  EnclosedPorch  3SsnPorch  ScreenPorch  \
count      8.0000     8.000000       8.000000        8.0          8.0   
mean      63.0000    95.625000      25.000000        0.0          0.0   
std      118.2298    89.162672      70.710678        0.0          0.0   
min        0.0000     0.000000       0.000000        0.0          0.0   
25%        0.0000    30.750000       0.000000        0.0          0.0   
50%        0.0000    82.000000       0.000000        0.0          0.0   
75%       54.0000   142.750000       0.000000        0.0          0.0   
max      288.0000   229.000000     200.000000        0.0          0.0   

       PoolArea  MiscVal      SalePrice  YearBuiltGrp  GarageYrBltGrp  
count       8.0      8.0       8.000000      8.000000        8.000000  
mean        0.0      0.0  236484.250000   1987.500000     1987.500000  
std         0.0      0.0   93964.474968     35.355339       35.355339  
min         0.0      0.0  182000.000000   1900.000000     1900.000000  
25%         0.0      0.0  196150.000000   2000.000000     2000.000000  
50%         0.0      0.0  203287.000000   2000.000000     2000.000000  
75%         0.0      0.0  221625.000000   2000.000000     2000.000000  
max         0.0      0.0  465000.000000   2000.000000     2000.000000  

[8 rows x 35 columns]

In [352]:
# if I compare the Sale Price percentile data grouped by MasVnrType, the 'NA' percentile closely matches 
# with Stone category. I can update the NA with Stone. But the next column MasVnrArea should have a value 
# filled as well. Since this value cant be derived from other columns, better to fill these as None
# If there are outliers, it should be removed later.

In [353]:
df['MasVnrArea'].isna().sum()

8

In [354]:
#lets fill these rows with None and 0 as MasVnrType and MasVrnArea

In [355]:
df['MasVnrArea'].fillna(0, axis = 0, inplace=True)

In [356]:
df['MasVnrType'].fillna('None', axis = 0, inplace=True)

In [357]:
df.groupby(['MasVnrType']).describe()

Id                                                        \
            count        mean         std   min     25%    50%      75%   
MasVnrType                                                                
BrkCmn       15.0  563.466667  365.587564  84.0  262.00  511.0   734.00   
BrkFace     445.0  707.314607  415.313097   1.0  343.00  696.0  1044.00   
None        872.0  740.263761  420.723235   2.0  384.75  746.0  1109.50   
Stone       128.0  764.164062  450.984501   7.0  336.25  805.0  1166.25   

                   MSSubClass             ... YearBuiltGrp          \
               max      count       mean  ...          75%     max   
MasVnrType                                ...                        
BrkCmn      1288.0       15.0  32.666667  ...       1900.0  1900.0   
BrkFace     1453.0      445.0  60.292135  ...       2000.0  2000.0   
None        1460.0      872.0  55.980505  ...       1900.0  2000.0   
Stone       1457.0      128.0  54.179688  ...       2000.0  2000.0   

           GarageYrBltGrp                                                  \
                    count         mean        std     min     25%     50%   
MasVnrType                                                                  
BrkCmn               15.0  1900.000000   0.000000  1900.0  1900.0  1900.0   
BrkFace             439.0  1931.207289  46.386803  1900.0  1900.0  1900.0   
None                797.0  1919.698871  39.797347  1900.0  1900.0  1900.0   
Stone               128.0  1984.375000  36.451888  1900.0  2000.0  2000.0   

                            
               75%     max  
MasVnrType                  
BrkCmn      1900.0  1900.0  
BrkFace     2000.0  2000.0  
None        1900.0  2000.0  
Stone       2000.0  2000.0  

[4 rows x 280 columns]

In [358]:
# Before update: 156221.891204	60708.262798	34900.0	118991.0	143000.0	181875.0	745000.0
# After update:  156958.243119	61491.688969	34900.0	119000.0	143125.0	184025.0	745000.0
# Min and Max values of Sale Price of MasVnrType "None" havent changed. But percentile values have slightly increased.

In [359]:
df.isna().any()[lambda x: x] 

BsmtQual          True
BsmtCond          True
BsmtExposure      True
BsmtFinType1      True
BsmtFinType2      True
Electrical        True
FireplaceQu       True
GarageType        True
GarageFinish      True
GarageQual        True
GarageCond        True
PoolQC            True
Fence             True
MiscFeature       True
GarageYrBltGrp    True
dtype: bool

In [360]:
# All the below columns have "NA" where there is no basement or no basement access. This is not a case of missing value
# but another category. Hence updating them as NOB for No basement.
#BsmtQual        True
#BsmtCond        True
#BsmtExposure    True
#BsmtFinType1    True
#BsmtFinType2    True

In [361]:
#before that checking the count of these missing rows
print('BsmtQual:' , df['BsmtQual'].isna().sum())
print('BsmtCond :' , df['BsmtCond'].isna().sum())
print('BsmtExposure :' , df['BsmtExposure'].isna().sum())
print('BsmtFinType1 :' , df['BsmtFinType1'].isna().sum())
print('BsmtFinType2 :' , df['BsmtFinType2'].isna().sum())

BsmtQual: 37
BsmtCond : 37
BsmtExposure : 38
BsmtFinType1 : 37
BsmtFinType2 : 38


In [362]:
temp_df=df[df['BsmtExposure'].isna()]

In [363]:
temp_df.shape

(38, 81)

In [364]:
# based on above analysis, we know that there is one row that has incorrect data Id - 949
# has unfinished basement but the basement exposure is marked as NA for No Basement. The relevant category
# for this could be No Exposure to Basement. Lets update that first and then update all other missing values as NOB for No basement.
# 949	Gd	TA	NaN	Unf	Unf

In [365]:
df.loc[df['Id']==949,'BsmtExposure']='No'

In [366]:
# Checking again
print('BsmtQual:' , df['BsmtQual'].isna().sum())
print('BsmtCond :' , df['BsmtCond'].isna().sum())
print('BsmtExposure :' , df['BsmtExposure'].isna().sum())
print('BsmtFinType1 :' , df['BsmtFinType1'].isna().sum())
print('BsmtFinType2 :' , df['BsmtFinType2'].isna().sum())

BsmtQual: 37
BsmtCond : 37
BsmtExposure : 37
BsmtFinType1 : 37
BsmtFinType2 : 38


In [367]:
# Do the same for BsmtFinType2
temp_df=df[df['BsmtFinType2'].isna()]
temp_df.loc[:, ['Id', 'BsmtQual', 'BsmtCond', 'BsmtExposure', 'BsmtFinType1','BsmtFinSF1' , 'BsmtFinType2','BsmtFinSF2' ]]

Id BsmtQual BsmtCond BsmtExposure BsmtFinType1  BsmtFinSF1  \
17      18      NaN      NaN          NaN          NaN           0   
39      40      NaN      NaN          NaN          NaN           0   
90      91      NaN      NaN          NaN          NaN           0   
102    103      NaN      NaN          NaN          NaN           0   
156    157      NaN      NaN          NaN          NaN           0   
182    183      NaN      NaN          NaN          NaN           0   
259    260      NaN      NaN          NaN          NaN           0   
332    333       Gd       TA           No          GLQ        1124   
342    343      NaN      NaN          NaN          NaN           0   
362    363      NaN      NaN          NaN          NaN           0   
371    372      NaN      NaN          NaN          NaN           0   
392    393      NaN      NaN          NaN          NaN           0   
520    521      NaN      NaN          NaN          NaN           0   
532    533      NaN      NaN          NaN          NaN           0   
533    534      NaN      NaN          NaN          NaN           0   
553    554      NaN      NaN          NaN          NaN           0   
646    647      NaN      NaN          NaN          NaN           0   
705    706      NaN      NaN          NaN          NaN           0   
736    737      NaN      NaN          NaN          NaN           0   
749    750      NaN      NaN          NaN          NaN           0   
778    779      NaN      NaN          NaN          NaN           0   
868    869      NaN      NaN          NaN          NaN           0   
894    895      NaN      NaN          NaN          NaN           0   
897    898      NaN      NaN          NaN          NaN           0   
984    985      NaN      NaN          NaN          NaN           0   
1000  1001      NaN      NaN          NaN          NaN           0   
1011  1012      NaN      NaN          NaN          NaN           0   
1035  1036      NaN      NaN          NaN          NaN           0   
1045  1046      NaN      NaN          NaN          NaN           0   
1048  1049      NaN      NaN          NaN          NaN           0   
1049  1050      NaN      NaN          NaN          NaN           0   
1090  1091      NaN      NaN          NaN          NaN           0   
1179  1180      NaN      NaN          NaN          NaN           0   
1216  1217      NaN      NaN          NaN          NaN           0   
1218  1219      NaN      NaN          NaN          NaN           0   
1232  1233      NaN      NaN          NaN          NaN           0   
1321  1322      NaN      NaN          NaN          NaN           0   
1412  1413      NaN      NaN          NaN          NaN           0   

     BsmtFinType2  BsmtFinSF2  
17            NaN           0  
39            NaN           0  
90            NaN           0  
102           NaN           0  
156           NaN           0  
182           NaN           0  
259           NaN           0  
332           NaN         479  
342           NaN           0  
362           NaN           0  
371           NaN           0  
392           NaN           0  
520           NaN           0  
532           NaN           0  
533           NaN           0  
553           NaN           0  
646           NaN           0  
705           NaN           0  
736           NaN           0  
749           NaN           0  
778           NaN           0  
868           NaN           0  
894           NaN           0  
897           NaN           0  
984           NaN           0  
1000          NaN           0  
1011          NaN           0  
1035          NaN           0  
1045          NaN           0  
1048          NaN           0  
1049          NaN           0  
1090          NaN           0  
1179          NaN           0  
1216          NaN           0  
1218          NaN           0  
1232          NaN           0  
1321          NaN           0  
1412          NaN           0

In [368]:
#Since the BsmtFinSF2 - area available for ID - 333, BsmtFinType2	 being NA is not valid. Hence updating it to be 'GLQ' .
df.loc[df['Id']==333,'BsmtFinType2']='GLQ'

In [369]:
# Checking again
print('BsmtQual:' , df['BsmtQual'].isna().sum())
print('BsmtCond :' , df['BsmtCond'].isna().sum())
print('BsmtExposure :' , df['BsmtExposure'].isna().sum())
print('BsmtFinType1 :' , df['BsmtFinType1'].isna().sum())
print('BsmtFinType2 :' , df['BsmtFinType2'].isna().sum())

BsmtQual: 37
BsmtCond : 37
BsmtExposure : 37
BsmtFinType1 : 37
BsmtFinType2 : 37


In [370]:
# Now all the missing values of these five columns can be safely updated as 'NOB' for No Basement category.
df['BsmtQual'].fillna('NOB', axis = 0, inplace=True)
df['BsmtCond'].fillna('NOB', axis = 0, inplace=True)
df['BsmtExposure'].fillna('NOB', axis = 0, inplace=True)
df['BsmtFinType1'].fillna('NOB', axis = 0, inplace=True)
df['BsmtFinType2'].fillna('NOB', axis = 0, inplace=True)

In [371]:
# Checking again
print('BsmtQual:' , df['BsmtQual'].isna().sum())
print('BsmtCond :' , df['BsmtCond'].isna().sum())
print('BsmtExposure :' , df['BsmtExposure'].isna().sum())
print('BsmtFinType1 :' , df['BsmtFinType1'].isna().sum())
print('BsmtFinType2 :' , df['BsmtFinType2'].isna().sum())

BsmtQual: 0
BsmtCond : 0
BsmtExposure : 0
BsmtFinType1 : 0
BsmtFinType2 : 0


In [372]:
#Checking for columns with null or missing values
df.isna().any()[lambda x: x] 

Electrical        True
FireplaceQu       True
GarageType        True
GarageFinish      True
GarageQual        True
GarageCond        True
PoolQC            True
Fence             True
MiscFeature       True
GarageYrBltGrp    True
dtype: bool

In [373]:
# Handling FirePlaceQu and Electrical
print('FirePlaceQu:' , df['FireplaceQu'].isna().sum())
print('Electrical :' , df['Electrical'].isna().sum())


FirePlaceQu: 690
Electrical : 1


In [374]:
# Only one record of Electrical column has value missing. This can be filled as there are possibly no 
# houses in US that are going to be built is going to be without Electrical circuit.
df[df['Electrical'].isna()].loc[: , 'Id':'Electrical']

Id  MSSubClass MSZoning  LotFrontage  LotArea Street    Alley  \
1379  1380          80       RL         73.0     9735   Pave  NoAlley   

     LotShape LandContour Utilities  ... BsmtFinType1 BsmtFinSF1 BsmtFinType2  \
1379      Reg         Lvl    AllPub  ...          Unf          0          Unf   

     BsmtFinSF2 BsmtUnfSF TotalBsmtSF Heating  HeatingQC  CentralAir  \
1379          0       384         384    GasA         Gd           Y   

     Electrical  
1379        NaN  

[1 rows x 41 columns]

In [375]:
df.groupby(['Electrical']).describe()

Id                                                         \
             count        mean         std    min     25%    50%      75%   
Electrical                                                                  
FuseA         94.0  690.351064  399.314485   16.0  386.50  593.5  1052.00   
FuseF         27.0  661.000000  473.297191    9.0  241.50  580.0  1051.00   
FuseP          3.0  184.000000  125.031996   40.0  143.50  247.0   256.00   
Mix            1.0  399.000000         NaN  399.0  399.00  399.0   399.00   
SBrkr       1334.0  735.726387  421.580160    1.0  368.25  742.5  1097.75   

                   MSSubClass              ... YearBuiltGrp          \
               max      count        mean  ...          75%     max   
Electrical                                 ...                        
FuseA       1459.0       94.0   47.712766  ...       1900.0  1900.0   
FuseF       1444.0       27.0   54.814815  ...       1900.0  1900.0   
FuseP        265.0        3.0  103.333333  ...       1900.0  1900.0   
Mix          399.0        1.0   30.000000  ...       1900.0  1900.0   
SBrkr       1460.0     1334.0   57.485007  ...       2000.0  2000.0   

           GarageYrBltGrp                                                  \
                    count         mean        std     min     25%     50%   
Electrical                                                                  
FuseA                81.0  1901.234568  11.111111  1900.0  1900.0  1900.0   
FuseF                22.0  1900.000000   0.000000  1900.0  1900.0  1900.0   
FuseP                 2.0  1900.000000   0.000000  1900.0  1900.0  1900.0   
Mix                   1.0  1900.000000        NaN  1900.0  1900.0  1900.0   
SBrkr              1272.0  1931.446541  46.448523  1900.0  1900.0  1900.0   

                            
               75%     max  
Electrical                  
FuseA       1900.0  2000.0  
FuseF       1900.0  1900.0  
FuseP       1900.0  1900.0  
Mix         1900.0  1900.0  
SBrkr       2000.0  2000.0  

[5 rows x 280 columns]

In [376]:
#Since majority of the houses fall under standard circuit system, lets update the missing value record 
# to be of std circuit.
df.loc[df['Id']==1380, 'Electrical']='SBrkr'

In [377]:
# Similarly handling FirePlaceQu
df[df['FireplaceQu'].isna()].loc[: , 'Id':'FireplaceQu']

Id  MSSubClass MSZoning  LotFrontage  LotArea Street    Alley  \
0        1          60       RL         65.0     8450   Pave  NoAlley   
5        6          50       RL         85.0    14115   Pave  NoAlley   
10      11          20       RL         70.0    11200   Pave  NoAlley   
12      13          20       RL          0.0    12968   Pave  NoAlley   
15      16          45       RM         51.0     6120   Pave  NoAlley   
17      18          90       RL         72.0    10791   Pave  NoAlley   
18      19          20       RL         66.0    13695   Pave  NoAlley   
19      20          20       RL         70.0     7560   Pave  NoAlley   
26      27          20       RL         60.0     7200   Pave  NoAlley   
29      30          30       RM         60.0     6324   Pave  NoAlley   
30      31          70  C (all)         50.0     8500   Pave     Pave   
31      32          20       RL          0.0     8544   Pave  NoAlley   
32      33          20       RL         85.0    11049   Pave  NoAlley   
36      37          20       RL        112.0    10859   Pave  NoAlley   
38      39          20       RL         68.0     7922   Pave  NoAlley   
39      40          90       RL         65.0     6040   Pave  NoAlley   
42      43          85       RL          0.0     9180   Pave  NoAlley   
43      44          20       RL          0.0     9200   Pave  NoAlley   
44      45          20       RL         70.0     7945   Pave  NoAlley   
47      48          20       FV         84.0    11096   Pave  NoAlley   
48      49         190       RM         33.0     4456   Pave  NoAlley   
49      50          20       RL         66.0     7742   Pave  NoAlley   
50      51          60       RL          0.0    13869   Pave  NoAlley   
52      53          90       RM        110.0     8472   Grvl  NoAlley   
56      57         160       FV         24.0     2645   Pave     Pave   
57      58          60       RL         89.0    11645   Pave  NoAlley   
59      60          20       RL         60.0     7200   Pave  NoAlley   
60      61          20       RL         63.0    13072   Pave  NoAlley   
61      62          75       RM         60.0     7200   Pave  NoAlley   
63      64          70       RM         50.0    10300   Pave  NoAlley   
64      65          60       RL          0.0     9375   Pave  NoAlley   
67      68          20       RL         72.0    10665   Pave  NoAlley   
68      69          30       RM         47.0     4608   Pave  NoAlley   
71      72          20       RL         69.0     7599   Pave  NoAlley   
73      74          20       RL         85.0    10200   Pave  NoAlley   
74      75          50       RM         60.0     5790   Pave  NoAlley   
75      76         180       RM         21.0     1596   Pave  NoAlley   
76      77          20       RL          0.0     8475   Pave  NoAlley   
77      78          50       RM         50.0     8635   Pave  NoAlley   
78      79          90       RL         72.0    10778   Pave  NoAlley   
79      80          50       RM         60.0    10440   Pave     Grvl   
81      82         120       RM         32.0     4500   Pave  NoAlley   
83      84          20       RL         80.0     8892   Pave  NoAlley   
87      88         160       FV         40.0     3951   Pave     Pave   
88      89          50  C (all)        105.0     8470   Pave  NoAlley   
89      90          20       RL         60.0     8070   Pave  NoAlley   
90      91          20       RL         60.0     7200   Pave  NoAlley   
91      92          20       RL         85.0     8500   Pave  NoAlley   
92      93          30       RL         80.0    13360   Pave     Grvl   
94      95          60       RL         69.0     9337   Pave  NoAlley   
96      97          20       RL         78.0    10264   Pave  NoAlley   
97      98          20       RL         73.0    10921   Pave  NoAlley   
98      99          30       RL         85.0    10625   Pave  NoAlley   
99     100          20       RL         77.0     9320   Pave  NoAl

In [378]:
#When there are no fireplaces, the quality is NA. This has to be converted into another category 'NOF' for No Fireplace
df['FireplaceQu'].fillna(value='NOF', axis=0, inplace=True)

In [379]:
# Handling FirePlaceQu and Electrical
print('FirePlaceQu:' , df['FireplaceQu'].isna().sum())
print('Electrical :' , df['Electrical'].isna().sum())

FirePlaceQu: 0
Electrical : 0


In [380]:
# Handling 
#GarageType      True
#GarageYrBlt     True
#GarageFinish    True
#GarageQual      True
#GarageCond      True
print('GarageType:' , df['GarageType'].isna().sum())
#print('GarageYrBlt :' , df['GarageYrBlt'].isna().sum())
print('GarageFinish:' , df['GarageFinish'].isna().sum())
print('GarageQual :' , df['GarageQual'].isna().sum())
print('GarageCond:' , df['GarageCond'].isna().sum())


GarageType: 81
GarageFinish: 81
GarageQual : 81
GarageCond: 81


In [381]:
df[df['GarageType'].isna()].loc[: , 'Id':'GarageCond']

Id  MSSubClass MSZoning  LotFrontage  LotArea Street    Alley  \
39      40          90       RL         65.0     6040   Pave  NoAlley   
48      49         190       RM         33.0     4456   Pave  NoAlley   
78      79          90       RL         72.0    10778   Pave  NoAlley   
88      89          50  C (all)        105.0     8470   Pave  NoAlley   
89      90          20       RL         60.0     8070   Pave  NoAlley   
99     100          20       RL         77.0     9320   Pave  NoAlley   
108    109          50       RM         85.0     8500   Pave  NoAlley   
125    126         190       RM         60.0     6780   Pave  NoAlley   
127    128          45       RM         55.0     4388   Pave  NoAlley   
140    141          20       RL         70.0    10500   Pave  NoAlley   
148    149          20       RL         63.0     7500   Pave  NoAlley   
155    156          50       RL         60.0     9600   Pave  NoAlley   
163    164          45       RL         55.0     5500   Pave  NoAlley   
165    166         190       RL         62.0    10106   Pave  NoAlley   
198    199          75       RM         92.0     5520   Pave  NoAlley   
210    211          30       RL         67.0     5604   Pave  NoAlley   
241    242          30       RM         40.0     3880   Pave  NoAlley   
250    251          30       RL         55.0     5350   Pave  NoAlley   
287    288          20       RL          0.0     8125   Pave  NoAlley   
291    292         190       RL         55.0     5687   Pave     Grvl   
307    308          50       RM          0.0     7920   Pave     Grvl   
375    376          30       RL          0.0    10020   Pave  NoAlley   
386    387          50       RL         58.0     8410   Pave  NoAlley   
393    394          30       RL          0.0     7446   Pave  NoAlley   
431    432          50       RM         60.0     5586   Pave  NoAlley   
434    435         180       RM         21.0     1890   Pave  NoAlley   
441    442          90       RL         92.0    12108   Pave  NoAlley   
464    465          20       RL         60.0     8430   Pave  NoAlley   
495    496          30  C (all)         60.0     7879   Pave  NoAlley   
520    521         190       RL         60.0    10800   Pave     Grvl   
528    529          30       RL         58.0     9098   Pave  NoAlley   
533    534          20       RL         50.0     5000   Pave  NoAlley   
535    536         190       RL         70.0     7000   Pave  NoAlley   
562    563          30       RL         63.0    13907   Pave  NoAlley   
582    583          90       RL         81.0    11841   Grvl  NoAlley   
613    614          20       RL         70.0     8402   Pave  NoAlley   
614    615         180       RM         21.0     1491   Pave  NoAlley   
620    621          30       RL         45.0     8248   Pave     Grvl   
635    636         190       RH         60.0    10896   Pave     Pave   
636    637          30       RM         51.0     6120   Pave  NoAlley   
638    639          30       RL         67.0     8777   Pave  NoAlley   
649    650         180       RM         21.0     1936   Pave  NoAlley   
705    706         190       RM         70.0     5600   Pave  NoAlley   
710    711          30       RL         56.0     4130   Pave  NoAlley   
738    739          90       RL         60.0    10800   Pave  NoAlley   
750    751          50       RM         55.0     8800   Pave     Grvl   
784    785          75       RM         35.0     6300   Pave     Grvl   
826    827          45       RM         50.0     6130   Pave  NoAlley   
843    844          90       RL         80.0     8000   Pave  NoAlley   
921    922          90       RL         67.0     8777   Pave  NoAlley   
942    943          90       RL         42.0     7711   Pave  NoAlley   
954    955          90       RL         35.0     9400   Pave  NoAlley   
960    961          20       RL         50.0     7207   Pave  NoAlley   
968    969          50       RM         50.0     5925   Pave  NoAl

In [382]:
#When there are no garages, all the columns related to garage are set to  NA. These have to be converted into another category 'NOG' for No Garage
df['GarageType'].fillna(value='NOG', axis=0, inplace=True)
#df['GarageYrBlt'].fillna(value='NOG', axis=0, inplace=True)
df['GarageFinish'].fillna(value='NOG', axis=0, inplace=True)
df['GarageQual'].fillna(value='NOG', axis=0, inplace=True)
df['GarageCond'].fillna(value='NOG', axis=0, inplace=True)


In [383]:
print('GarageType:' , df['GarageType'].isna().sum())
#print('GarageYrBlt :' , df['GarageYrBlt'].isna().sum())
print('GarageFinish:' , df['GarageFinish'].isna().sum())
print('GarageQual :' , df['GarageQual'].isna().sum())
print('GarageCond:' , df['GarageCond'].isna().sum())

GarageType: 0
GarageFinish: 0
GarageQual : 0
GarageCond: 0


In [384]:
#Checking for columns with null or missing values
df.isna().any()[lambda x: x] 

PoolQC            True
Fence             True
MiscFeature       True
GarageYrBltGrp    True
dtype: bool

In [385]:
# Handling 
#PoolQC         True
#Fence          True
#MiscFeature    True
print('PoolQC:' , df['PoolQC'].isna().sum())
print('Fence :' , df['Fence'].isna().sum())
print('MiscFeature:' , df['MiscFeature'].isna().sum())


PoolQC: 1453
Fence : 1179
MiscFeature: 1406


In [386]:
df[df['PoolQC'].isna()].loc[: , 'Id':'PoolQC']

Id  MSSubClass MSZoning  LotFrontage  LotArea Street    Alley  \
0        1          60       RL         65.0     8450   Pave  NoAlley   
1        2          20       RL         80.0     9600   Pave  NoAlley   
2        3          60       RL         68.0    11250   Pave  NoAlley   
3        4          70       RL         60.0     9550   Pave  NoAlley   
4        5          60       RL         84.0    14260   Pave  NoAlley   
5        6          50       RL         85.0    14115   Pave  NoAlley   
6        7          20       RL         75.0    10084   Pave  NoAlley   
7        8          60       RL          0.0    10382   Pave  NoAlley   
8        9          50       RM         51.0     6120   Pave  NoAlley   
9       10         190       RL         50.0     7420   Pave  NoAlley   
10      11          20       RL         70.0    11200   Pave  NoAlley   
11      12          60       RL         85.0    11924   Pave  NoAlley   
12      13          20       RL          0.0    12968   Pave  NoAlley   
13      14          20       RL         91.0    10652   Pave  NoAlley   
14      15          20       RL          0.0    10920   Pave  NoAlley   
15      16          45       RM         51.0     6120   Pave  NoAlley   
16      17          20       RL          0.0    11241   Pave  NoAlley   
17      18          90       RL         72.0    10791   Pave  NoAlley   
18      19          20       RL         66.0    13695   Pave  NoAlley   
19      20          20       RL         70.0     7560   Pave  NoAlley   
20      21          60       RL        101.0    14215   Pave  NoAlley   
21      22          45       RM         57.0     7449   Pave     Grvl   
22      23          20       RL         75.0     9742   Pave  NoAlley   
23      24         120       RM         44.0     4224   Pave  NoAlley   
24      25          20       RL          0.0     8246   Pave  NoAlley   
25      26          20       RL        110.0    14230   Pave  NoAlley   
26      27          20       RL         60.0     7200   Pave  NoAlley   
27      28          20       RL         98.0    11478   Pave  NoAlley   
28      29          20       RL         47.0    16321   Pave  NoAlley   
29      30          30       RM         60.0     6324   Pave  NoAlley   
30      31          70  C (all)         50.0     8500   Pave     Pave   
31      32          20       RL          0.0     8544   Pave  NoAlley   
32      33          20       RL         85.0    11049   Pave  NoAlley   
33      34          20       RL         70.0    10552   Pave  NoAlley   
34      35         120       RL         60.0     7313   Pave  NoAlley   
35      36          60       RL        108.0    13418   Pave  NoAlley   
36      37          20       RL        112.0    10859   Pave  NoAlley   
37      38          20       RL         74.0     8532   Pave  NoAlley   
38      39          20       RL         68.0     7922   Pave  NoAlley   
39      40          90       RL         65.0     6040   Pave  NoAlley   
40      41          20       RL         84.0     8658   Pave  NoAlley   
41      42          20       RL        115.0    16905   Pave  NoAlley   
42      43          85       RL          0.0     9180   Pave  NoAlley   
43      44          20       RL          0.0     9200   Pave  NoAlley   
44      45          20       RL         70.0     7945   Pave  NoAlley   
45      46         120       RL         61.0     7658   Pave  NoAlley   
46      47          50       RL         48.0    12822   Pave  NoAlley   
47      48          20       FV         84.0    11096   Pave  NoAlley   
48      49         190       RM         33.0     4456   Pave  NoAlley   
49      50          20       RL         66.0     7742   Pave  NoAlley   
50      51          60       RL          0.0    13869   Pave  NoAlley   
51      52          50       RM         52.0     6240   Pave  NoAlley   
52      53          90       RM        110.0     8472   Grvl  NoAlley   
53      54          20       RL         68.0    50271   Pave  NoAl

In [387]:
df[df['PoolArea']==0]

Id  MSSubClass MSZoning  LotFrontage  LotArea Street    Alley  \
0        1          60       RL         65.0     8450   Pave  NoAlley   
1        2          20       RL         80.0     9600   Pave  NoAlley   
2        3          60       RL         68.0    11250   Pave  NoAlley   
3        4          70       RL         60.0     9550   Pave  NoAlley   
4        5          60       RL         84.0    14260   Pave  NoAlley   
5        6          50       RL         85.0    14115   Pave  NoAlley   
6        7          20       RL         75.0    10084   Pave  NoAlley   
7        8          60       RL          0.0    10382   Pave  NoAlley   
8        9          50       RM         51.0     6120   Pave  NoAlley   
9       10         190       RL         50.0     7420   Pave  NoAlley   
10      11          20       RL         70.0    11200   Pave  NoAlley   
11      12          60       RL         85.0    11924   Pave  NoAlley   
12      13          20       RL          0.0    12968   Pave  NoAlley   
13      14          20       RL         91.0    10652   Pave  NoAlley   
14      15          20       RL          0.0    10920   Pave  NoAlley   
15      16          45       RM         51.0     6120   Pave  NoAlley   
16      17          20       RL          0.0    11241   Pave  NoAlley   
17      18          90       RL         72.0    10791   Pave  NoAlley   
18      19          20       RL         66.0    13695   Pave  NoAlley   
19      20          20       RL         70.0     7560   Pave  NoAlley   
20      21          60       RL        101.0    14215   Pave  NoAlley   
21      22          45       RM         57.0     7449   Pave     Grvl   
22      23          20       RL         75.0     9742   Pave  NoAlley   
23      24         120       RM         44.0     4224   Pave  NoAlley   
24      25          20       RL          0.0     8246   Pave  NoAlley   
25      26          20       RL        110.0    14230   Pave  NoAlley   
26      27          20       RL         60.0     7200   Pave  NoAlley   
27      28          20       RL         98.0    11478   Pave  NoAlley   
28      29          20       RL         47.0    16321   Pave  NoAlley   
29      30          30       RM         60.0     6324   Pave  NoAlley   
30      31          70  C (all)         50.0     8500   Pave     Pave   
31      32          20       RL          0.0     8544   Pave  NoAlley   
32      33          20       RL         85.0    11049   Pave  NoAlley   
33      34          20       RL         70.0    10552   Pave  NoAlley   
34      35         120       RL         60.0     7313   Pave  NoAlley   
35      36          60       RL        108.0    13418   Pave  NoAlley   
36      37          20       RL        112.0    10859   Pave  NoAlley   
37      38          20       RL         74.0     8532   Pave  NoAlley   
38      39          20       RL         68.0     7922   Pave  NoAlley   
39      40          90       RL         65.0     6040   Pave  NoAlley   
40      41          20       RL         84.0     8658   Pave  NoAlley   
41      42          20       RL        115.0    16905   Pave  NoAlley   
42      43          85       RL          0.0     9180   Pave  NoAlley   
43      44          20       RL          0.0     9200   Pave  NoAlley   
44      45          20       RL         70.0     7945   Pave  NoAlley   
45      46         120       RL         61.0     7658   Pave  NoAlley   
46      47          50       RL         48.0    12822   Pave  NoAlley   
47      48          20       FV         84.0    11096   Pave  NoAlley   
48      49         190       RM         33.0     4456   Pave  NoAlley   
49      50          20       RL         66.0     7742   Pave  NoAlley   
50      51          60       RL          0.0    13869   Pave  NoAlley   
51      52          50       RM         52.0     6240   Pave  NoAlley   
52      53          90       RM        110.0     8472   Grvl  NoAlley   
53      54          20       RL         68.0    50271   Pave  NoAl

In [388]:
#When there is no Pool Area or pool access, the pool quality is termed as 'NA'.
# Lets update this value to 'NOP' for No Pool
df['PoolQC'].fillna(value='NOP', axis=0, inplace=True)

In [389]:
#When there is no Fence, the column Fence is termed as 'NA'.
# Lets update this value to 'NOFen' for No Fence
df['Fence'].fillna(value='NOFen', axis=0, inplace=True)

In [390]:
df['MiscFeature'].isna().sum()

1406

In [391]:
df[df['MiscVal']==0].count()

Id                1408
MSSubClass        1408
MSZoning          1408
LotFrontage       1408
LotArea           1408
Street            1408
Alley             1408
LotShape          1408
LandContour       1408
Utilities         1408
LotConfig         1408
LandSlope         1408
Neighborhood      1408
Condition1        1408
Condition2        1408
BldgType          1408
HouseStyle        1408
OverallQual       1408
OverallCond       1408
RoofStyle         1408
RoofMatl          1408
Exterior1st       1408
Exterior2nd       1408
MasVnrType        1408
MasVnrArea        1408
ExterQual         1408
ExterCond         1408
Foundation        1408
BsmtQual          1408
BsmtCond          1408
BsmtExposure      1408
BsmtFinType1      1408
BsmtFinSF1        1408
BsmtFinType2      1408
BsmtFinSF2        1408
BsmtUnfSF         1408
TotalBsmtSF       1408
Heating           1408
HeatingQC         1408
CentralAir        1408
Electrical        1408
1stFlrSF          1408
2ndFlrSF          1408
LowQualFinS

In [392]:
# When there is a Misc feature, there has to be a Misc value also. But it seems there are two rows that 
# have Misc features not as NA but the Misc Val as 0. Lets address this first and take care of NA values.
df.loc[(df['MiscVal']==0) & (df['MiscFeature'].notna()), 'Id': 'MiscVal']

Id  MSSubClass MSZoning  LotFrontage  LotArea Street    Alley  \
873    874          40       RL         60.0    12144   Pave  NoAlley   
1200  1201          20       RL         71.0     9353   Pave  NoAlley   

     LotShape LandContour Utilities  ... WoodDeckSF OpenPorchSF EnclosedPorch  \
873       Reg         Lvl    AllPub  ...          0          28             0   
1200      Reg         Lvl    AllPub  ...          0           0             0   

     3SsnPorch ScreenPorch PoolArea PoolQC  Fence  MiscFeature MiscVal  
873          0           0        0    NOP  NOFen         Othr       0  
1200         0           0        0    NOP  NOFen         Shed       0  

[2 rows x 73 columns]

In [393]:
#update the MiscFeature to 'NOM' for No Misc Feature to these two rows.
df.loc[df['Id']==874, 'MiscFeature'] = 'NOM'
df.loc[df['Id']==1201, 'MiscFeature']='NOM'

In [394]:
df['MiscFeature'].isna().sum()

1406

In [395]:
df.loc[(df['MiscVal']==0) & (df['MiscFeature'].notna()), 'Id': 'MiscVal']


Id  MSSubClass MSZoning  LotFrontage  LotArea Street    Alley  \
873    874          40       RL         60.0    12144   Pave  NoAlley   
1200  1201          20       RL         71.0     9353   Pave  NoAlley   

     LotShape LandContour Utilities  ... WoodDeckSF OpenPorchSF EnclosedPorch  \
873       Reg         Lvl    AllPub  ...          0          28             0   
1200      Reg         Lvl    AllPub  ...          0           0             0   

     3SsnPorch ScreenPorch PoolArea PoolQC  Fence  MiscFeature MiscVal  
873          0           0        0    NOP  NOFen          NOM       0  
1200         0           0        0    NOP  NOFen          NOM       0  

[2 rows x 73 columns]

In [396]:
df['MiscFeature'].fillna(value='NOM', axis=0, inplace=True)

In [397]:
df['MiscFeature'].isna().sum()

0

In [398]:
df.isna().any()[lambda x: x] 

GarageYrBltGrp    True
dtype: bool

In [399]:
df['GarageYrBltGrp'].fillna(value='NOG', axis=0, inplace=True)

In [400]:
df.describe()

Id   MSSubClass  LotFrontage        LotArea  OverallQual  \
count  1460.000000  1460.000000  1460.000000    1460.000000  1460.000000   
mean    730.500000    56.897260    57.623288   10516.828082     6.099315   
std     421.610009    42.300571    34.664304    9981.264932     1.382997   
min       1.000000    20.000000     0.000000    1300.000000     1.000000   
25%     365.750000    20.000000    42.000000    7553.500000     5.000000   
50%     730.500000    50.000000    63.000000    9478.500000     6.000000   
75%    1095.250000    70.000000    79.000000   11601.500000     7.000000   
max    1460.000000   190.000000   313.000000  215245.000000    10.000000   

       OverallCond   MasVnrArea   BsmtFinSF1   BsmtFinSF2    BsmtUnfSF  ...  \
count  1460.000000  1460.000000  1460.000000  1460.000000  1460.000000  ...   
mean      5.575342   103.117123   443.639726    46.549315   567.240411  ...   
std       1.112799   180.731373   456.098091   161.319273   441.866955  ...   
min       1.000000     0.000000     0.000000     0.000000     0.000000  ...   
25%       5.000000     0.000000     0.000000     0.000000   223.000000  ...   
50%       5.000000     0.000000   383.500000     0.000000   477.500000  ...   
75%       6.000000   164.250000   712.250000     0.000000   808.000000  ...   
max       9.000000  1600.000000  5644.000000  1474.000000  2336.000000  ...   

        GarageArea   WoodDeckSF  OpenPorchSF  EnclosedPorch    3SsnPorch  \
count  1460.000000  1460.000000  1460.000000    1460.000000  1460.000000   
mean    472.980137    94.244521    46.660274      21.954110     3.409589   
std     213.804841   125.338794    66.256028      61.119149    29.317331   
min       0.000000     0.000000     0.000000       0.000000     0.000000   
25%     334.500000     0.000000     0.000000       0.000000     0.000000   
50%     480.000000     0.000000    25.000000       0.000000     0.000000   
75%     576.000000   168.000000    68.000000       0.000000     0.000000   
max    1418.000000   857.000000   547.000000     552.000000   508.000000   

       ScreenPorch     PoolArea       MiscVal      SalePrice  YearBuiltGrp  
count  1460.000000  1460.000000   1460.000000    1460.000000   1460.000000  
mean     15.060959     2.758904     43.489041  180921.195890   1925.547945  
std      55.757415    40.177307    496.123024   79442.502883     45.924079  
min       0.000000     0.000000      0.000000   34900.000000   1800.000000  
25%       0.000000     0.000000      0.000000  129975.000000   1900.000000  
50%       0.000000     0.000000      0.000000  163000.000000   1900.000000  
75%       0.000000     0.000000      0.000000  214000.000000   2000.000000  
max     480.000000   738.000000  15500.000000  755000.000000   2000.000000  

[8 rows x 34 columns]

#### Data Cleanup

In [401]:
df.drop(['Id'], axis=1, inplace=True)

In [402]:
cols_drop=[]
for col in df.columns:
    max_pct = np.max(df[col].value_counts(normalize=True)*100)
    if max_pct>90:
        cols_drop.append(col)

In [403]:
df.drop(cols_drop, axis=1, inplace=True)

In [404]:
df['MSSubClass']=df['MSSubClass'].map(str)

In [405]:
(df==0).sum(axis=0) #columns wih all or more zeros

MSSubClass           0
MSZoning             0
LotFrontage        259
LotArea              0
LotShape             0
LandContour          0
LotConfig            0
Neighborhood         0
Condition1           0
BldgType             0
HouseStyle           0
OverallQual          0
OverallCond          0
RoofStyle            0
Exterior1st          0
Exterior2nd          0
MasVnrType           0
MasVnrArea         869
ExterQual            0
ExterCond            0
Foundation           0
BsmtQual             0
BsmtCond             0
BsmtExposure         0
BsmtFinType1         0
BsmtFinSF1         467
BsmtFinType2         0
BsmtFinSF2        1293
BsmtUnfSF          118
TotalBsmtSF         37
HeatingQC            0
1stFlrSF             0
2ndFlrSF           829
GrLivArea            0
BsmtFullBath       856
FullBath             9
HalfBath           913
BedroomAbvGr         6
KitchenQual          0
TotRmsAbvGrd         0
Fireplaces         690
FireplaceQu          0
GarageType           0
GarageFinis

In [406]:
temp_df1=((df==0).sum(axis=1)[lambda x: x>10]) #columns wih all or more zeros)

In [407]:
df.drop(temp_df1.index, axis=0, inplace=True)

In [408]:
#remove columns with more than 50% rows zeros
df.drop(['MasVnrType', 'MasVnrArea', 'BsmtFinSF2', 'BsmtFinType2',
        '2ndFlrSF','BsmtFullBath', 'HalfBath', 'Fireplaces', 'WoodDeckSF', 'OpenPorchSF',
        'EnclosedPorch'], axis = 1, inplace=True)

In [409]:
cols_drop=[]
for col in df.columns:
    max_pct = np.max(df[col].value_counts(normalize=True)*100)
    if max_pct>90:
        cols_drop.append(col)
df.drop(cols_drop, axis=1, inplace=True)

In [410]:
df['OverallQual']=df['OverallQual'].map(str)
df['OverallCond']=df['OverallCond'].map(str)

In [411]:
df['FullBath']=df['FullBath'].map(str)
df['BedroomAbvGr']=df['BedroomAbvGr'].map(str)
df['TotRmsAbvGrd']=df['TotRmsAbvGrd'].map(str)
df['GarageCars']=df['GarageCars'].map(str)

In [412]:
df.drop(['MSZoning', 'LotShape', 'LotConfig', 'Condition1',
        'BldgType'], axis=1, inplace=True)

In [413]:
df.drop(['OverallCond', 'RoofStyle', 'ExterCond', 'BsmtExposure',
        ], axis=1, inplace=True)

In [414]:
df.drop(['Fence', 'SaleType', 'SaleCondition'
        ], axis=1, inplace=True)

In [415]:
df.drop(['YearBuiltGrp'], axis=1, inplace=True) #dropping as YearRemodelled should accomodate the Built as well

#### Adding dummy variables for categorical variables

In [416]:
MSSubClass=pd.get_dummies(df['MSSubClass'], drop_first=True)
for col in MSSUbClass.columns:
    MSSubClass.rename(columns={col: 'MSSubClass_'+col}, inplace=True)
    df=pd.concat([df,MSSubClass], axis=1)

In [417]:
Neighborhood=pd.get_dummies(df['Neighborhood'], drop_first=True)
for col in Neighborhood.columns:
    Neighborhood.rename(columns={col: 'Neighborhood'+col}, inplace=True)
    df=pd.concat([df,Neighborhood], axis=1)


In [418]:
HouseStyle=pd.get_dummies(df['HouseStyle'], drop_first=True)
for col in HouseStyle.columns:
    HouseStyle.rename(columns={col: 'HouseStyle'+col}, inplace=True)
    df=pd.concat([df,HouseStyle], axis=1)

In [419]:
OverallQual=pd.get_dummies(df['OverallQual'], drop_first=True)
for col in OverallQual.columns:
    OverallQual.rename(columns={col: 'OverallQual'+col}, inplace=True)
    df=pd.concat([df,OverallQual], axis=1)

In [420]:
Remodeled=pd.get_dummies(df['Remodeled'], drop_first=True)
for col in Remodeled.columns:
    Remodeled.rename(columns={col: 'Remodeled'+col}, inplace=True)
    df=pd.concat([df,Remodeled], axis=1)

In [421]:
df['new']=np.where((df['Exterior1st']== df['Exterior2nd']), np.nan, df['Exterior2nd'])

In [422]:
df['new'].isna().sum()

1205

In [423]:
df.drop(['Exterior2nd', 'new'], axis=1,inplace=True)

In [424]:
Exterior1st=pd.get_dummies(df['Exterior1st'], drop_first=True)
for col in Exterior1st.columns:
    Exterior1st.rename(columns={col: 'Exterior1st'+col}, inplace=True)
    df=pd.concat([df,Exterior1st], axis=1)

In [425]:
ExterQual=pd.get_dummies(df['ExterQual'], drop_first=True)
for col in ExterQual.columns:
    ExterQual.rename(columns={col: 'ExterQual'+col}, inplace=True)
    df=pd.concat([df,ExterQual], axis=1)

In [426]:
Foundation=pd.get_dummies(df['Foundation'], drop_first=True)
for col in Foundation.columns:
    Foundation.rename(columns={col: 'Foundation'+col}, inplace=True)
    df=pd.concat([df,Foundation], axis=1)

In [427]:
BsmtQual=pd.get_dummies(df['BsmtQual'], drop_first=True)
for col in BsmtQual.columns:
    BsmtQual.rename(columns={col: 'BsmtQual'+col}, inplace=True)
    df=pd.concat([df,BsmtQual], axis=1)

In [428]:
BsmtFinType1=pd.get_dummies(df['BsmtFinType1'], drop_first=True)
for col in BsmtFinType1.columns:
    BsmtFinType1.rename(columns={col: 'BsmtFinType1'+col}, inplace=True)
    df=pd.concat([df,BsmtFinType1], axis=1)

In [429]:
HeatingQC=pd.get_dummies(df['HeatingQC'], drop_first=True)
for col in HeatingQC.columns:
    HeatingQC.rename(columns={col: 'HeatingQC'+col}, inplace=True)
    df=pd.concat([df,HeatingQC], axis=1)

In [430]:
FullBath=pd.get_dummies(df['FullBath'], drop_first=True)
for col in FullBath.columns:
    FullBath.rename(columns={col: 'FullBath'+col}, inplace=True)
    df=pd.concat([df,FullBath], axis=1)

In [431]:
BedroomAbvGr=pd.get_dummies(df['BedroomAbvGr'], drop_first=True)
for col in BedroomAbvGr.columns:
    BedroomAbvGr.rename(columns={col: 'BedroomAbvGr'+col}, inplace=True)
    df=pd.concat([df,BedroomAbvGr], axis=1)

In [432]:
KitchenQual=pd.get_dummies(df['KitchenQual'], drop_first=True)
for col in KitchenQual.columns:
    KitchenQual.rename(columns={col: 'KitchenQual'+col}, inplace=True)
    df=pd.concat([df,KitchenQual], axis=1)

In [433]:
TotRmsAbvGrd=pd.get_dummies(df['TotRmsAbvGrd'], drop_first=True)
for col in TotRmsAbvGrd.columns:
    TotRmsAbvGrd.rename(columns={col: 'TotRmsAbvGrd'+col}, inplace=True)
    df=pd.concat([df,TotRmsAbvGrd], axis=1)

In [434]:
FireplaceQu=pd.get_dummies(df['FireplaceQu'], drop_first=True)
for col in FireplaceQu.columns:
    FireplaceQu.rename(columns={col: 'FireplaceQu'+col}, inplace=True)
    df=pd.concat([df,FireplaceQu], axis=1)

In [435]:
GarageType=pd.get_dummies(df['GarageType'], drop_first=True)
for col in GarageType.columns:
    GarageType.rename(columns={col: 'GarageType'+col}, inplace=True)
    df=pd.concat([df,GarageType], axis=1)

In [436]:
df['GarageYrBltGrp']=df['GarageYrBltGrp'].map(str)

In [437]:
GarageYrBltGrp=pd.get_dummies(df['GarageYrBltGrp'], drop_first=True)
for col in GarageYrBltGrp.columns:
    GarageYrBltGrp.rename(columns={col: 'GarageYrBltGrp'+col}, inplace=True)
    df=pd.concat([df,GarageYrBltGrp], axis=1)

In [438]:
GarageFinish=pd.get_dummies(df['GarageFinish'], drop_first=True)
for col in GarageFinish.columns:
    GarageFinish.rename(columns={col: 'GarageFinish'+col}, inplace=True)
    df=pd.concat([df,GarageFinish], axis=1)

In [439]:
GarageCars=pd.get_dummies(df['GarageCars'], drop_first=True)
for col in GarageCars.columns:
    GarageCars.rename(columns={col: 'GarageCars'+col}, inplace=True)
    df=pd.concat([df,GarageCars], axis=1)

In [440]:
MoSoldGrp=pd.get_dummies(df['MoSoldGrp'], drop_first=True)
for col in MoSoldGrp.columns:
    MoSoldGrp.rename(columns={col: 'MoSoldGrp'+col}, inplace=True)
    df=pd.concat([df,MoSoldGrp], axis=1)

In [441]:
YrSoldGrp=pd.get_dummies(df['YrSoldGrp'], drop_first=True)
for col in YrSoldGrp.columns:
    YrSoldGrp.rename(columns={col: 'YrSoldGrp'+col}, inplace=True)
    df=pd.concat([df,YrSoldGrp], axis=1)

In [442]:
df.drop(['YrSoldGrp','MoSoldGrp', 'GarageCars', 'GarageFinish', 'GarageYrBltGrp', 'GarageType','FireplaceQu',
        'TotRmsAbvGrd', 'KitchenQual','BedroomAbvGr','FullBath', 'HeatingQC', 'BsmtFinType1','BsmtQual',
        'Foundation', 'ExterQual', 'Exterior1st'], axis=1, inplace=True)

In [443]:
df.columns

Index(['MSSubClass', 'LotFrontage', 'LotArea', 'LandContour', 'Neighborhood',
       'HouseStyle', 'OverallQual', 'BsmtFinSF1', 'BsmtUnfSF', 'TotalBsmtSF',
       ...
       'GarageCars1', 'GarageCars2', 'GarageCars3', '4', 'GarageCars1',
       'GarageCars2', 'GarageCars3', 'GarageCars4', 'MoSoldGrp2ndhalf',
       'YrSoldGrpBefore2008'],
      dtype='object', length=1431)

In [444]:
df.drop(['Remodeled'],axis=1, inplace=True)

In [445]:
df.drop(['OverallQual'],axis=1, inplace=True)

In [446]:
df.drop(['Neighborhood'],axis=1, inplace=True)

In [447]:
df.drop( ['HouseStyle'], axis=1, inplace=True)

In [448]:
df.drop( ['LandContour', 'MSSubClass'], axis=1, inplace=True)

In [449]:
X=df.copy()

In [450]:
y=X.pop('SalePrice')


In [451]:
X.drop

<bound method DataFrame.drop of       LotFrontage  LotArea  BsmtFinSF1  BsmtUnfSF  TotalBsmtSF  1stFlrSF  \
0            65.0     8450         706        150          856       856   
1            80.0     9600         978        284         1262      1262   
2            68.0    11250         486        434          920       920   
3            60.0     9550         216        540          756       961   
4            84.0    14260         655        490         1145      1145   
5            85.0    14115         732         64          796       796   
6            75.0    10084        1369        317         1686      1694   
7             0.0    10382         859        216         1107      1107   
8            51.0     6120           0        952          952      1022   
9            50.0     7420         851        140          991      1077   
10           70.0    11200         906        134         1040      1040   
11           85.0    11924         998        177       

In [452]:
# scaling the features - necessary before using Ridge or Lasso
from sklearn.preprocessing import scale

# storing column names in cols, since column names are (annoyingly) lost after 
# scaling (the df is converted to a numpy array)
cols = X.columns
X = pd.DataFrame(scale(X))
X.columns = cols
X.columns

Index(['LotFrontage', 'LotArea', 'BsmtFinSF1', 'BsmtUnfSF', 'TotalBsmtSF',
       '1stFlrSF', 'GrLivArea', 'GarageArea', '160', '180',
       ...
       'GarageCars1', 'GarageCars2', 'GarageCars3', '4', 'GarageCars1',
       'GarageCars2', 'GarageCars3', 'GarageCars4', 'MoSoldGrp2ndhalf',
       'YrSoldGrpBefore2008'],
      dtype='object', length=1424)

In [453]:
# split into train and test
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, 
                                                    train_size=0.7,
                                                    test_size = 0.3, random_state=100)

## 3. Model Building and Evaluation

## Linear Regression

Let's now try predicting car prices, a dataset using linear regression.

In [454]:
# Instantiate
lm = LinearRegression()

# Fit a line
lm.fit(X_train, y_train)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None,
         normalize=False)

In [455]:
# Print the coefficients and intercept
print(lm.intercept_)
print(lm.coef_)

184061.3461928934
[-1.95846668e+03  3.18746955e+03 -5.71388680e+03 ... -2.82373537e+15
 -4.77886520e+01  1.25305630e+02]


In [456]:
from sklearn.metrics import r2_score, mean_squared_error

In [457]:
y_pred_train = lm.predict(X_train)
y_pred_test = lm.predict(X_test)

metric = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric.append(mse_test_lr**0.5)

0.8255433305658315
0.8190301359472401
986266184788.26
562515445884.5248
1001285466.7901117
1329823749.1359923


## Ridge and Lasso Regression

Let's now try predicting House prices, a dataset used in simple linear regression, to perform ridge and lasso regression.

In [458]:
# list of alphas to tune - if value too high it will lead to underfitting, if it is too low, 
# it will not handle the overfitting
params = {'alpha': [0.0001, 0.001, 0.01, 0.05, 0.1, 
 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0, 2.0, 3.0, 
 4.0, 5.0, 6.0, 7.0, 8.0, 9.0, 10.0, 20, 50, 100, 500, 1000 ]}

ridge = Ridge()

# cross validation
folds = 5
model_cv = GridSearchCV(estimator = ridge, 
                        param_grid = params, 
                        scoring= 'neg_mean_absolute_error',  
                        cv = folds, 
                        return_train_score=True,
                        verbose = 1)            
model_cv.fit(X_train, y_train) 
#https://scikit-learn.org/stable/modules/model_evaluation.html

Fitting 5 folds for each of 28 candidates, totalling 140 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 140 out of 140 | elapsed:    7.9s finished


GridSearchCV(cv=5, error_score='raise-deprecating',
       estimator=Ridge(alpha=1.0, copy_X=True, fit_intercept=True, max_iter=None,
   normalize=False, random_state=None, solver='auto', tol=0.001),
       fit_params=None, iid='warn', n_jobs=None,
       param_grid={'alpha': [0.0001, 0.001, 0.01, 0.05, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, 9.0, 10.0, 20, 50, 100, 500, 1000]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score=True,
       scoring='neg_mean_absolute_error', verbose=1)

In [459]:
# Printing the best hyperparameter alpha
print(model_cv.best_params_)

{'alpha': 100}


In [460]:
#Fitting Ridge model for alpha = 10 and printing coefficients which have been penalised
alpha = 100
ridge = Ridge(alpha=alpha)

ridge.fit(X_train, y_train)
print(ridge.coef_)

[-1853.96097962  4068.08688064   294.40275334 ...   388.98688147
  -248.1638863   -408.06229909]


In [461]:
# Lets calculate some metrics such as R2 score, RSS and RMSE
y_pred_train = ridge.predict(X_train)
y_pred_test = ridge.predict(X_test)

metric2 = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric2.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric2.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric2.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric2.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric2.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric2.append(mse_test_lr**0.5)

0.8672955840289991
0.8574639093078429
750225706295.8649
443050300280.71704
761650463.2445328
1047400237.070253


## Lasso

In [462]:
lasso = Lasso()

# cross validation
model_cv = GridSearchCV(estimator = lasso, 
                        param_grid = params, 
                        scoring= 'neg_mean_absolute_error', 
                        cv = folds, 
                        return_train_score=True,
                        verbose = 1)            

model_cv.fit(X_train, y_train) 

Fitting 5 folds for each of 28 candidates, totalling 140 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 140 out of 140 | elapsed:  2.0min finished


GridSearchCV(cv=5, error_score='raise-deprecating',
       estimator=Lasso(alpha=1.0, copy_X=True, fit_intercept=True, max_iter=1000,
   normalize=False, positive=False, precompute=False, random_state=None,
   selection='cyclic', tol=0.0001, warm_start=False),
       fit_params=None, iid='warn', n_jobs=None,
       param_grid={'alpha': [0.0001, 0.001, 0.01, 0.05, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, 9.0, 10.0, 20, 50, 100, 500, 1000]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score=True,
       scoring='neg_mean_absolute_error', verbose=1)

In [463]:
# Printing the best hyperparameter alpha
print(model_cv.best_params_)

{'alpha': 500}


In [464]:
#Fitting Ridge model for alpha = 100 and printing coefficients which have been penalised

alpha =500

lasso = Lasso(alpha=alpha)
        
lasso.fit(X_train, y_train) 

Lasso(alpha=500, copy_X=True, fit_intercept=True, max_iter=1000,
   normalize=False, positive=False, precompute=False, random_state=None,
   selection='cyclic', tol=0.0001, warm_start=False)

In [465]:
lasso.coef_

array([-1.08360765e+03,  4.67934751e+03,  6.20590139e+02, ...,
        1.34008076e-03, -0.00000000e+00, -0.00000000e+00])

In [466]:
# Lets calculate some metrics such as R2 score, RSS and RMSE

y_pred_train = lasso.predict(X_train)
y_pred_test = lasso.predict(X_test)

metric3 = []
r2_train_lr = r2_score(y_train, y_pred_train)
print(r2_train_lr)
metric3.append(r2_train_lr)

r2_test_lr = r2_score(y_test, y_pred_test)
print(r2_test_lr)
metric3.append(r2_test_lr)

rss1_lr = np.sum(np.square(y_train - y_pred_train))
print(rss1_lr)
metric3.append(rss1_lr)

rss2_lr = np.sum(np.square(y_test - y_pred_test))
print(rss2_lr)
metric3.append(rss2_lr)

mse_train_lr = mean_squared_error(y_train, y_pred_train)
print(mse_train_lr)
metric3.append(mse_train_lr**0.5)

mse_test_lr = mean_squared_error(y_test, y_pred_test)
print(mse_test_lr)
metric3.append(mse_test_lr**0.5)

0.8546135483055924
0.8557978817661489
821921807275.2117
448228876450.7177
834438383.0205195
1059642733.9260466


In [467]:
# Creating a table which contain all the metrics

lr_table = {'Metric': ['R2 Score (Train)','R2 Score (Test)','RSS (Train)','RSS (Test)',
                       'MSE (Train)','MSE (Test)'], 
        'Linear Regression': metric
        }

lr_metric = pd.DataFrame(lr_table ,columns = ['Metric', 'Linear Regression'] )

rg_metric = pd.Series(metric2, name = 'Ridge Regression')
ls_metric = pd.Series(metric3, name = 'Lasso Regression')

final_metric = pd.concat([lr_metric, rg_metric, ls_metric], axis = 1)

final_metric

Metric  Linear Regression  Ridge Regression  Lasso Regression
0  R2 Score (Train)       8.255433e-01      8.672956e-01      8.546135e-01
1   R2 Score (Test)       8.190301e-01      8.574639e-01      8.557979e-01
2       RSS (Train)       9.862662e+11      7.502257e+11      8.219218e+11
3        RSS (Test)       5.625154e+11      4.430503e+11      4.482289e+11
4       MSE (Train)       3.164310e+04      2.759802e+04      2.888665e+04
5        MSE (Test)       3.646675e+04      3.236356e+04      3.255215e+04

### Lets observe the changes in the coefficients after regularization

In [468]:
betas = pd.DataFrame(index=X.columns)

In [469]:
betas.rows = X.columns

In [470]:
betas['Linear'] = lm.coef_
betas['Ridge'] = ridge.coef_
betas['Lasso'] = lasso.coef_

In [471]:
pd.set_option('display.max_rows', None)
betas.head(68)

Linear         Ridge         Lasso
LotFrontage    -1.958467e+03  -1853.960980  -1083.607653
LotArea         3.187470e+03   4068.086881   4679.347506
BsmtFinSF1     -5.713887e+03    294.402753    620.590139
BsmtUnfSF      -9.349825e+03  -3993.502635  -4014.167271
TotalBsmtSF     3.383985e+03    523.936557      0.000000
1stFlrSF        1.039414e+03   5243.009192   1259.540039
GrLivArea       1.845558e+04  10464.468194  26707.557645
GarageArea     -1.515271e+03     69.514918      0.000000
160            -2.564438e+17    -95.494249  -3102.051335
180             2.536488e+17     26.513987     -0.000000
190            -6.981219e+16     82.789361   -291.957835
20             -1.357056e+17    915.879636   6505.050059
30             -8.178304e+14    299.927370    790.670840
40             -1.454731e+17    117.007175     12.057881
45             -1.500664e+17    105.587209      0.000000
50              2.875138e+17    523.510751      0.000000
60             -1.925422e+17    648.083024      0.000000
70              3.305095e+17    303.498003     -0.000000
75              1.370917e+17    398.027317    430.057122
80             -2.715638e+16    167.722204    427.489022
85             -2.040033e+17     92.791671      0.000000
90              1.700630e+17    -14.020722  -1047.707863
160            -1.930947e+16    -95.494249   -790.101439
MSSubClass_180 -8.825533e+16     26.513987     -0.000000
190            -1.438667e+17     82.789361   -317.880891
20             -3.938448e+16    915.879636     70.657119
30             -1.355329e+16    299.927370     31.060321
40              7.730838e+16    117.007175      1.355713
45              4.950131e+16    105.587209      0.000000
50              1.369025e+17    523.510751      0.000000
60              1.206379e+17    648.083024      0.000000
70              8.121627e+16    303.498003     -0.000000
75             -2.025671e+17    398.027317     88.022878
80             -1.842355e+16    167.722204     23.857108
85             -9.497643e+16     92.791671      0.000000
90              4.265310e+16    -14.020722    -70.353479
160            -1.060192e+17    -95.494249   -260.237522
MSSubClass_180 -9.260384e+16     26.513987     -0.000000
MSSubClass_190 -1.447294e+17     82.789361    -84.188548
20              2.353014e+17    915.879636     14.963506
30              1.364227e+17    299.927370      5.088735
40              6.804196e+17    117.007175      0.091949
45              1.547171e+17    105.587209      0.000000
50              1.475689e+17    523.510751      0.000000
60              5.645779e+17    648.083024      0.000000
70              1.367709e+17    303.498003     -0.000000
75             -7.857039e+16    398.027317      2.500060
80             -3.709626e+16    167.722204      3.982911
85              2.282140e+17     92.791671      0.000000
90             -3.873893e+16    -14.020722    -12.017810
160             6.313094e+17    -95.494249   -116.740706
MSSubClass_180  1.268503e+17     26.513987     -0.000000
MSSubClass_190  1.085070e+17     82.789361    -78.875452
MSSubClass_20   2.670966e+17    915.879636      1.626178
30             -2.950888e+17    299.927370      0.469329
40             -2.737678e+17    117.007175      0.007926
45              2.188516e+17    105.587209      0.000000
50             -3.133744e+17    523.510751      0.000000
60             -7.873599e+16    648.083024      0.000000
70             -1.991841e+17    303.498003     -0.000000
75              2.925133e+14    398.027317      0.217638
80             -2.320676e+17    167.722204      0.280652
85              4.368831e+16     92.791671      0.000000
90              1.245562e+17    -14.020722     -6.606969
160            -3.310254e+16    -95.494249    -27.071659
MSSubClass_180 -2.270361e+17     26.513987     -0.000000
MSSubClass_190 -8.374405e+16     82.789361    -17.025245
MSSubClass_20   2.751326e+17    915.879636      0.016620